# Setup

# Import functions

In [14]:
import pandas as pd
import glob
import json
import datetime as dt
from urllib.parse import unquote
# from bs4 import BeautifulSoup
import os
import shutil
from sentinelhub import SHConfig
import datetime
import numpy as np
import matplotlib.pyplot as plt
import sys
from datetime import timedelta
sys.path.insert(0,'..')
from sentinelhub import MimeType, CRS, BBox, SentinelHubRequest, SentinelHubDownloadClient, DataCollection, bbox_to_dimensions, DownloadRequest
from epiweeks import Week, Year
import epiweeks
from datetime import date
import glob, shutil

In [15]:
#import shutil
#!shutil.rmtree('satellite.extractor')
#!git clone https://github.com/sebasmos/satellite.extractor.git

# Install dependencies
#%cd satellite.extractor/

#! python setup.py build
#! python setup.py install
#! pip install -r requirements.txt

#%cd ..
cred = pd.read_csv("/Users/sebasmos/Desktop/satellite.extractor/satellite_extractor/satellite-extractor-dockerized/data_config/SentinelHub-credentials.csv")
CLIENT_ID = str(cred.iloc[0,:][0])
CLIENT_SECRET = str(cred.iloc[1,:][0])
LATITUDE = 3.4400
LONGITUDE= -76.5197
TIMESTAPS = [2016,2018]
# projection = CRS.WGS84
IMAGE_FORMAT = "tiff"
CODE = 5555
LENGTH = 750
RESOLUTION = 10
COORDINATES_PATH = "/Users/sebasmos/Desktop/satellite.extractor/data/10_municipalities_full.csv"
service_account = 'ee-account@mit-hst-dengue.iam.gserviceaccount.com'
 

In [16]:
!ls

DATASET
PART_1_satellite_imagery_augmentation.ipynb
PART_2_satellite_imagery_augmentation.ipynb
Reading_GCP_from_Colab.ipynb
bands_analysis.ipynb
convert_to_rgb.ipynb
create_Cloud2CloudlesDataset.ipynb
data
download_images.ipynb
downloader_sentinel_5_cities.ipynb
find_collections.ipynb
hash_print.ipynb
image_analysis.ipynb
local_downloader_sentinel_all_cities.ipynb
output.pdf
quickstart_api.ipynb
satellite_extractor.ipynb
satellite_images_hashing.ipynb
sentinelhub-py
viz_many_folders.ipynb


In [17]:
%cd satellite.extractor
!ls

[Errno 2] No such file or directory: 'satellite.extractor'
/Users/sebasmos/Desktop/satellite.extractor/notebooks
DATASET
PART_1_satellite_imagery_augmentation.ipynb
PART_2_satellite_imagery_augmentation.ipynb
Reading_GCP_from_Colab.ipynb
bands_analysis.ipynb
convert_to_rgb.ipynb
create_Cloud2CloudlesDataset.ipynb
data
download_images.ipynb
downloader_sentinel_5_cities.ipynb
find_collections.ipynb
hash_print.ipynb
image_analysis.ipynb
local_downloader_sentinel_all_cities.ipynb
output.pdf
quickstart_api.ipynb
satellite_extractor.ipynb
satellite_images_hashing.ipynb
sentinelhub-py
viz_many_folders.ipynb


In [18]:
from linux.request_multiple_images_linux import download_multiple_images

ModuleNotFoundError: No module named 'linux'

In [ ]:
!pwd

/home/datascience/Data Fusion/experiments/violence_prediction/Dataset/Satellite/satellite.extractor


In [ ]:
!ls

data	 distributions.egg-info  linux	    README.md	      scripts	src
DATASET  __init__.py		 notebooks  requirements.txt  setup.py


# 10 cities

In [ ]:
from dotenv import load_dotenv

load_dotenv()
CLIENT_ID = os.getenv('CLIENT_ID')
CLIENT_SECRET = os.getenv('CLIENT_SECRET')

In [ ]:
path = '../Coordinates/'

In [ ]:
# dic = pd.read_csv(path + 'coordinates512_top_10_municipalities.csv')
# dic = dict(zip(dic['Municipality'], dic.square))
# # Convert the values to lists
# dic = {key: [float(x) for x in value.strip('[]').split(', ')] for key, value in dic.items()}

# dic
COORDINATES_PATH = "/Users/sebasmos/Desktop/satellite.extractor/data/10_municipalities_full.csv"
# Read the CSV file
# df = pd.read_csv(COORDINATES_PATH)
# df['municipalities'] = df['municipalities'].astype(str)
dic = pd.read_csv(COORDINATES_PATH)
dic = dict(zip(dic['municipalities'], dic.coordinates))
# Convert the values to lists
dic = {key: [float(x) for x in value.strip('[]').split(', ')] for key, value in dic.items()}

# Convert the coordinates string to a list and create a dictionary
# dic = {}
# for index, row in df.iterrows():
#     municipality_code = str(row['municipalities'])
#     coordinates_str = row['coordinates']
#     coordinates_list = json.loads(coordinates_str)
#     dic[municipality_code] = coordinates_list

# Print the resulting dictionary
print(dic)

{68276: [-73.13152717841406, 7.035967219961829, -73.06396519775542, 7.103445747318065], 5088: [-75.59177622386039, 6.298167220061509, -75.52431637390244, 6.365645747318065]}


In [ ]:
img_format = "tiff"
'''
    # REAL DATA FOR COLOMBIA
    initial_year = 2015
    end_year = 2018
    years = list(range(initial_year,end_year))
    first_2015_week = 44
    end_year = 2020
    start_2015 = Week(initial_year,first_2015_week).startdate()
    weeks_2015 = list(range(first_2015_week, 53))
    weeks = list(range(1,53))
    
    # TESTING DATA
    
    initial_year = 2017
    end_year = 2018
    years = list(range(initial_year,end_year))
    first_2015_week = 44
    end_year = 2018
    start_2015 = Week(initial_year,first_2015_week).startdate()
    weeks_2015 = list(range(first_2015_week, 53))
    weeks = list(range(1,10))
'''
   # Define the range of years
initial_year = 2016
end_year = 2019
years = list(range(initial_year,end_year))
first_2015_week = 44

start_2015 = Week(initial_year,first_2015_week).startdate()

weeks_2015 = list(range(first_2015_week, 53))
weeks = list(range(1,53))


root_images = "/data/"
       
temporal_path = os.path.abspath(os.getcwd()) + root_images  
    
if not os.path.isdir(temporal_path):
    os.makedirs(temporal_path)
    print("Creating temporal data folder")
        
print(f"Number of cities: {len(dic)}")
print(f"Range: {years}")
print(f"Weeks 2015: {weeks_2015}")

Number of cities: 2
Range: [2016, 2017, 2018]
Weeks 2015: [44, 45, 46, 47, 48, 49, 50, 51, 52]


In [ ]:
img_format = "tiff"

# Define the range of years
initial_year = 2016
end_year = 2023
years = list(range(initial_year,end_year))
first_2015_week = 44

start_2015 = Week(initial_year,first_2015_week).startdate()

weeks_2015 = list(range(first_2015_week, 53))

#weeks = list(range(1,53))
weeks = {}
# Iterate through the years and calculate the number of epiweeks
for year in range(initial_year, end_year):
    num_epiweeks = 0
    for week_num in range(1, 54):
        try:
            epiweek = epiweeks.Week(year, week_num)
            num_epiweeks += 1
        except ValueError:
            # This week doesn't exist for this year
            pass
    weeks[year] = list(range(1, num_epiweeks + 1))

root_images = "/data/"
# Get the absolute path of the current working directory
current_directory = os.getcwd()

temporal_path = os.path.abspath(os.path.join(current_directory, root_images[1:]))

if not os.path.isdir(temporal_path):
    os.makedirs(temporal_path)
    print("Creating temporal data folder")

print(f"Number of cities: {len(dic)}")
print(f"Range: {years}")
print(f"Weeks 2015: {weeks_2015}")

Number of cities: 2
Range: [2016, 2017, 2018, 2019, 2020, 2021, 2022]
Weeks 2015: [44, 45, 46, 47, 48, 49, 50, 51, 52]


In [ ]:
def get_folder_ID(root_images, img_format):

    #print(root_images, img_format)

    walker = "." + root_images

    for root, dirs, files in os.walk(walker, topdown=True):
        for name in files:
            path = os.path.join(root, name)
            if "response" in path:

                folder_path = path.replace("/" + "response." + img_format, "")

    return folder_path

In [ ]:
def get_request_individual(request_file, img_format):
    with open(request_file, 'r') as req:
        print(request_file)
        json_decode = json.load(req)
        dataFilter = json_decode['request']["payload"]["input"]["data"][0]
        timeRanges = dataFilter["dataFilter"]["timeRange"]
        start = timeRanges["from"].split("T")[0]
        end = timeRanges["to"].split("T")[0]
        time_stamp = start + "_to_" + end # best image calculated on this interval
        name_image = "image_" +   start
        print(name_image)
        data = {
            "start": start,
            "end": end,
            "time_stamp": time_stamp,
            "url": request_file,
            }

        df = pd.DataFrame(data, index =['date'])

        # Update name of files using JSON timestamp filter
        response_img = request_file.split("request.json")[0] + "response.tiff"# + "."+ img_format
        image_path = os.path.join(response_img).replace('response', name_image )
        print("{0} renamed to {1}".format(response_img, image_path))
        shutil.move(response_img, image_path)

        return df

In [ ]:

def get_epi_weeks(start):
    
    n_chunks = 53

    tdelta =  timedelta(days = 7)
    
    edges = [(start + i*tdelta) for i in range(n_chunks)]
    
    return [(edges[i], edges[i+1]) for i in range(len(edges)-1)]

def download_multiple_images(coordinates, start, year, CLIENT_ID, CLIENT_SECRET):
    # put here your credentials
    CLIENT_ID = CLIENT_ID
    CLIENT_SECRET = CLIENT_SECRET

    config = SHConfig()

    if CLIENT_ID and CLIENT_SECRET:
        config.sh_client_id = CLIENT_ID
        config.sh_client_secret=CLIENT_SECRET
    
    if not config.sh_client_id or not config.sh_client_secret:
        print("Warning! To use Process API, please provide the credentials (OAuth client ID and client secret).")

    resolution = 10
    bbox = BBox(bbox=coordinates, crs=CRS.WGS84)
    bbox_size = bbox_to_dimensions(bbox, resolution=resolution)

    print(f'Image shape at {resolution} m resolution: {bbox_size} pixels')

    slots = get_epi_weeks(start)

    print('Weekly time windows:\n')
    for slot in slots:
        print(slot)

    evalscript_true_color = """

        //VERSION=3
        function setup() {
            return {
                input: [{
                    bands: ["B02", "B03", "B04", "B05", "B06", "B07", "B08"]
                }],
                output: {
                    bands: 7
                }
            };
        }
        function evaluatePixel(sample) {
            return [sample.B08, 
                    sample.B07, 
                    sample.B06, 
                    sample.B05, 
                    sample.B04, 
                    sample.B03, 
                    sample.B02];
        }
    """
    
    evalscript_rgb ="""
    //VERSION=3
    
    function setup() {
      return {
        input: ["B02", "B03", "B04"],
        output: { bands: 3 }
      };
    }
    
    function evaluatePixel(sample) {
      return [2.5 * sample.B04, 2.5 * sample.B03, 2.5 * sample.B02];
    }
    """
    '''Check if directory exists, if not, create it'''
    
    # You should change 'test' to your preferred folder.
    # If folder doesn't exist, then create it.
    
    # if windows: 
    path = os.path.abspath(os.getcwd()) + "\\data"  + "\\" + year
    # if linux: path = os.path.abspath(os.getcwd()) + "/data"  + "/" year
    
    if not os.path.isdir(path):
        os.makedirs(path)
        print("created folder : ", path)
    else:
        print(path, "Folder already exists. Rewriting*")
        pass
 


In [ ]:
from satellite_extractor.algorithms import download_multiple_images_16_bit_forward_backward,download_image, get_folder_ID#, get_request_individual
def get_images(coordenates, years, weeks, weeks_2015, img_format, root_images, CLIENT_ID, CLIENT_SECRET):
    # Download data
    folder_path = ""
    for year in years:
        if year == 2015:
            for week in weeks_2015:
                print(f"Year: {year} - week: {week}")
                # Set starting date for given year based on
                start = Week(year, week).startdate()
                # Download individual images
                download_multiple_images(coordenates, start, str(year), CLIENT_ID, CLIENT_SECRET)
                # Obtain ID as the last-obtained response.tiff file, "real-time"
                folder_path = get_folder_ID(root_images, img_format)
                # Rename image based on JSON timestamp filter
                dates = get_request_individual(folder_path+"/request.json", img_format)
                # Clean folders which contain black images
                path_to_blank_ids  = "." + root_images + "/" + str(year) + "/*/*"
                ids = glob.glob(path_to_blank_ids)
                for idx in ids:
                    if "response" in idx:
                        folder_path = idx.replace("/" + "response." + img_format, "")
                        #print(folder_path)
                        shutil.rmtree(folder_path)
                ids = glob.glob(path_to_blank_ids)
                #print("ids available: ", ids)

                #flag =  [idx if ("response" in idx) for idx in ids]
        #elif year ==2016:
        else:
            for week in weeks[year]:
                print(f"Year: {year} - week: {week}")
                # Set starting date for given year based on
                start = Week(year, week).startdate()
                # Download individual images
                download_multiple_images(coordenates, start, str(year), CLIENT_ID, CLIENT_SECRET)
                # Obtain ID as the last-obtained response.tiff file, "real-time"
                folder_path = get_folder_ID(root_images, img_format)
                # Rename image based on JSON timestamp filter
                dates = get_request_individual(folder_path+"/request.json", img_format)
                # Clean folders which contain black images
                path_to_blank_ids  = "." + root_images + "/" + str(year) + "/*/*"
                ids = glob.glob(path_to_blank_ids)
                for idx in ids:
                    if "response" in idx:
                        folder_path = idx.replace("/" + "response." + img_format, "")
                        print(folder_path)
                        shutil.rmtree(folder_path)
                ids = glob.glob(path_to_blank_ids)


In [ ]:
for i in dic:
    
    print("Clean the temporal data folder")
    shutil.rmtree(root_images[1:])
    os.makedirs(temporal_path)
    
    print(f"City: {i} - Coordinates: {dic[i]}")

    current_coor = dic[i]

    city_str = "DATASET" + "/" + str(i)

    if not os.path.exists(city_str):
        os.makedirs(city_str)

    # Download images on given range
    get_images(current_coor, years, weeks, weeks_2015, img_format, root_images, CLIENT_ID, CLIENT_SECRET)

    # Move to structured folder in DATASETS
    root_images_store = "." + root_images
    dataset_store = "./" + city_str
    for root, dirs, files in os.walk(root_images_store, topdown=True):
        for name in files:
            path = os.path.join(root, name)
            #print(path)
            if img_format in path and not dataset_store in path:
                shutil.copy(path, dataset_store)

images = glob.glob(dataset_store+"/*")

Clean the temporal data folder
City: 68276 - Coordinates: [-73.13152717841406, 7.035967219961829, -73.06396519775542, 7.103445747318065]
Year: 2016 - week: 1
Image shape at 10 m resolution: (743, 749) pixels
Weekly time windows:

(datetime.date(2016, 1, 3), datetime.date(2016, 1, 10))
(datetime.date(2016, 1, 10), datetime.date(2016, 1, 17))
(datetime.date(2016, 1, 17), datetime.date(2016, 1, 24))
(datetime.date(2016, 1, 24), datetime.date(2016, 1, 31))
(datetime.date(2016, 1, 31), datetime.date(2016, 2, 7))
(datetime.date(2016, 2, 7), datetime.date(2016, 2, 14))
(datetime.date(2016, 2, 14), datetime.date(2016, 2, 21))
(datetime.date(2016, 2, 21), datetime.date(2016, 2, 28))
(datetime.date(2016, 2, 28), datetime.date(2016, 3, 6))
(datetime.date(2016, 3, 6), datetime.date(2016, 3, 13))
(datetime.date(2016, 3, 13), datetime.date(2016, 3, 20))
(datetime.date(2016, 3, 20), datetime.date(2016, 3, 27))
(datetime.date(2016, 3, 27), datetime.date(2016, 4, 3))
(datetime.date(2016, 4, 3), datetim

UnboundLocalError: local variable 'y' referenced before assignment

In [ ]:
#shutil.rmtree("DATASET")
#shutil.rmtree("data")

In [ ]:
def plot_image(image, factor=1.0, clip_range = None, **kwargs):
    """
    Utility function for plotting RGB images.
    """
    fig, ax = plt.subplots(nrows=1, ncols=1, figsize=(15, 15))
    if clip_range is not None:
        ax.imshow(np.clip(image * factor, *clip_range), **kwargs)
    else:
        ax.imshow(image * factor, **kwargs)
    ax.set_xticks([])
    ax.set_yticks([])


In [ ]:
images

['./DATASET/Cúcuta/image_2021-09-12.tiff',
 './DATASET/Cúcuta/image_2017-07-30.tiff',
 './DATASET/Cúcuta/image_2020-03-01.tiff',
 './DATASET/Cúcuta/image_2020-01-26.tiff',
 './DATASET/Cúcuta/image_2019-10-20.tiff',
 './DATASET/Cúcuta/image_2021-06-13.tiff',
 './DATASET/Cúcuta/image_2017-11-19.tiff',
 './DATASET/Cúcuta/image_2016-11-20.tiff',
 './DATASET/Cúcuta/image_2017-07-16.tiff',
 './DATASET/Cúcuta/image_2022-09-04.tiff',
 './DATASET/Cúcuta/image_2021-03-28.tiff',
 './DATASET/Cúcuta/image_2016-07-31.tiff',
 './DATASET/Cúcuta/image_2017-02-19.tiff',
 './DATASET/Cúcuta/image_2016-04-10.tiff',
 './DATASET/Cúcuta/image_2022-02-20.tiff',
 './DATASET/Cúcuta/image_2020-05-03.tiff',
 './DATASET/Cúcuta/image_2020-03-15.tiff',
 './DATASET/Cúcuta/image_2017-03-12.tiff',
 './DATASET/Cúcuta/image_2016-04-03.tiff',
 './DATASET/Cúcuta/image_2021-05-02.tiff',
 './DATASET/Cúcuta/image_2020-10-11.tiff',
 './DATASET/Cúcuta/image_2021-06-27.tiff',
 './DATASET/Cúcuta/image_2018-12-23.tiff',
 './DATASET

In [ ]:
from skimage import io
import numpy as np
import cv2

ncols = 4
nrows = 3

aspect_ratio = 1
subplot_kw = {'xticks': [], 'yticks': [], 'frame_on': False}

fig, axs = plt.subplots(ncols=ncols, nrows=nrows, figsize=(5 * ncols * aspect_ratio, 5 * nrows),
                        subplot_kw=subplot_kw)

for idx, path in enumerate(images):
    if idx == 12:
        break
    else:
        ax = axs[idx // ncols][idx % ncols]
        image = io.imread(path)
        image = np.array(image)
        image = image[:,:,1:4]
        ax.imshow(np.clip(image * 2.5/255, 0, 1))

# Remove any empty subplots if num_images is less than ncols * nrows
for idx in range(len(images), ncols * nrows):
    ax = axs[idx // ncols][idx % ncols]
    ax.axis('off')

plt.tight_layout()
plt.show()

### Move Dataset to Parent Directory

In [ ]:
import os
import shutil

# Move DATASET to parent directory
source_directory = 'DATASET'
destination_directory = '../'

# Check if the source directory exists
if os.path.exists(source_directory):
    try:
        # Move the source directory to the destination
        shutil.move(source_directory, destination_directory)
        print(f"Moved '{source_directory}' to '{destination_directory}' successfully.")
    except Exception as e:
        print(f"An error occurred: {e}")
else:
    print(f"The source directory '{source_directory}' does not exist.")

Moved 'DATASET' to '../' successfully.


In [ ]:
!pwd

/home/datascience/Data Fusion/experiments/violence_prediction/Dataset/Satellite/satellite.extractor


# Visualize 5 imgs per folder

In [ ]:
import glob
import os
import matplotlib.pyplot as plt
from skimage import io
import numpy as np
from matplotlib.backends.backend_pdf import PdfPages
import random

data = "/home/datascience/Data Fusion/experiments/violence_prediction/Dataset/Satellite/DATASET"
folders = glob.glob(os.path.join(data, '*'))
pdf_pages = PdfPages("output.pdf")

def read_tiff(img_path, resize_ratio=None, resizing=True, normalize=True, printing=True):
    img = io.imread(img_path)
    img_F = img.copy()

    path_img = os.path.basename(img_path)
    if normalize:
        CHANNELS = range(12)
        img_F = np.dstack([
            skimage.exposure.rescale_intensity(img_F[:, :, c], out_range=(0, 1))
            for c in CHANNELS])
    if printing:
        print(f"(origin shape: {path_img}: {img.shape} -> rescale: {str(img_F.shape)}) - Range -> [{img_F.min(), img_F.max()}]")
    return img_F

for i, folder in enumerate(folders):
    tiff_files = glob.glob(os.path.join(folder, '*.tiff'))
    random.shuffle(tiff_files)
    selected_files = tiff_files[:10]

    fig, axes = plt.subplots(2, 5, figsize=(12, 6))

    for j, tiff_file in enumerate(selected_files):
        image = read_tiff(tiff_file)
        image = np.array(image)
        image = image[:, :, 1:4]
        axes[j // 5, j % 5].imshow(image)

        folder_name = os.path.basename(folder)
        file_name = os.path.basename(tiff_file)
        title = f"{folder_name} \n{file_name}"
        axes[j // 5, j % 5].set_title(title)
        axes[j // 5, j % 5].axis('off')

    pdf_pages.savefig(fig)
    plt.close(fig)

pdf_pages.close()


(origin shape: image_2019-08-04.tiff: (509, 510, 12) -> rescale: (509, 510, 12)) - Range -> [(0.0, 1.0)]
(origin shape: image_2021-06-13.tiff: (509, 510, 12) -> rescale: (509, 510, 12)) - Range -> [(0.0, 1.0)]
(origin shape: image_2019-12-22.tiff: (509, 510, 12) -> rescale: (509, 510, 12)) - Range -> [(0.0, 1.0)]
(origin shape: image_2017-10-15.tiff: (509, 510, 12) -> rescale: (509, 510, 12)) - Range -> [(0.0, 1.0)]
(origin shape: image_2017-12-31.tiff: (509, 510, 12) -> rescale: (509, 510, 12)) - Range -> [(0.0, 1.0)]
(origin shape: image_2016-04-24.tiff: (509, 510, 12) -> rescale: (509, 510, 12)) - Range -> [(0.0, 1.0)]
(origin shape: image_2020-05-10.tiff: (509, 510, 12) -> rescale: (509, 510, 12)) - Range -> [(0.0, 1.0)]
(origin shape: image_2019-12-08.tiff: (509, 510, 12) -> rescale: (509, 510, 12)) - Range -> [(0.0, 1.0)]
(origin shape: image_2021-11-21.tiff: (509, 510, 12) -> rescale: (509, 510, 12)) - Range -> [(0.0, 1.0)]
(origin shape: image_2016-05-08.tiff: (509, 510, 12) ->